In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/ranzcr-clip-catheter-line-classification/sample_submission.csv
/kaggle/input/ranzcr-clip-catheter-line-classification/train_annotations.csv
/kaggle/input/ranzcr-clip-catheter-line-classification/train.csv
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/05-1881.tfrec
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/12-1881.tfrec
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/11-1881.tfrec
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/04-1881.tfrec
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/00-1881.tfrec
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/08-1881.tfrec
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/15-1881.tfrec
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/02-1881.tfrec
/kaggle/input/ranzcr-clip-catheter-line-classification/train_tfrecords/03-1881.tfrec
/kaggle/input/ra

In [2]:
train = pd.read_csv("../input/ranzcr-clip-catheter-line-classification/train.csv")
train.head()

StudyInstanceUID  ETT - Abnormal  \
0  1.2.826.0.1.3680043.8.498.26697628953273228189...               0   
1  1.2.826.0.1.3680043.8.498.46302891597398758759...               0   
2  1.2.826.0.1.3680043.8.498.23819260719748494858...               0   
3  1.2.826.0.1.3680043.8.498.68286643202323212801...               0   
4  1.2.826.0.1.3680043.8.498.10050203009225938259...               0   

   ETT - Borderline  ETT - Normal  NGT - Abnormal  NGT - Borderline  \
0                 0             0               0                 0   
1                 0             1               0                 0   
2                 0             0               0                 0   
3                 0             0               0                 0   
4                 0             0               0                 0   

   NGT - Incompletely Imaged  NGT - Normal  CVC - Abnormal  CVC - Borderline  \
0                          0             1               0                 0   
1                          1             0               0                 0   
2                          0             0               0                 1   
3                          0             0               1                 0   
4                          0             0               0                 0   

   CVC - Normal  Swan Ganz Catheter Present  PatientID  
0             0                           0  ec89415d1  
1             1                           0  bf4c6da3c  
2             0                           0  3fc1c97e5  
3             0                           0  c31019814  
4             1                           0  207685cd1

In [3]:
train_annot = pd.read_csv("../input/ranzcr-clip-catheter-line-classification/train_annotations.csv")

In [4]:
train_annot.head()

StudyInstanceUID             label  \
0  1.2.826.0.1.3680043.8.498.12616281126973421762...      CVC - Normal   
1  1.2.826.0.1.3680043.8.498.12616281126973421762...      CVC - Normal   
2  1.2.826.0.1.3680043.8.498.72921907356394389969...  CVC - Borderline   
3  1.2.826.0.1.3680043.8.498.11697104485452001927...      CVC - Normal   
4  1.2.826.0.1.3680043.8.498.87704688663091069148...      NGT - Normal   

                                                data  
0  [[1487, 1279], [1477, 1168], [1472, 1052], [14...  
1  [[1328, 7], [1347, 101], [1383, 193], [1400, 2...  
2  [[801, 1207], [812, 1112], [823, 1023], [842, ...  
3  [[1366, 961], [1411, 861], [1453, 751], [1508,...  
4  [[1862, 14], [1845, 293], [1801, 869], [1716, ...

In [5]:
import albumentations as A
from albumentations.pytorch import ToTensorV2
from albumentations import ImageOnlyTransform
import os
import random
import torch
import numpy as np

In [6]:
class CFG:
    debug=False
    print_freq=100
    num_workers=4
    model_name="resnet200d"
    size=512
    scheduler="ReduceLROnPlateau"
    
    epochs=3
    lr=1e-4
    factor=0.2 # ReduceLROnPlateau
    patience=4 # ReduceLROnPlateau
    eps=1e-6 # ReduceLROnPlateau
    T_max=6
    min_lr=1e-6
    batch_size=16
    weight_decay=1e-6
    gradient_accumulation_steps=1
    max_grad_norm=1000
    seed=42
    target_size=11
    target_cols=['ETT - Abnormal', 'ETT - Borderline', 'ETT - Normal',
                 'NGT - Abnormal', 'NGT - Borderline', 'NGT - Incompletely Imaged', 'NGT - Normal', 
                 'CVC - Abnormal', 'CVC - Borderline', 'CVC - Normal',
                 'Swan Ganz Catheter Present']
    n_fold=4
    trn_fold=[0, 1, 2, 3]
    train=True

In [7]:
if CFG.debug:
    CFG.epochs=1
    train = train.sample(n=100, random_state=CFG.seed).reset_index(drop=True)

In [8]:
def get_transform(*, data):
    if data == 'train':
        return A.Compose([
            A.RandomResizedCrop(CFG.size, CFG.size, scale=(0.9, 1), p=1),
            A.HorizontalFlip(p=0.5),
            A.ShiftScaleRotate(p=0.5),
            A.HueSaturationValue(hue_shift_limit=10, sat_shift_limit=10, val_shift_limit=10, p=0.7),
            A.RandomBrightnessContrast(brightness_limit=(-0.2, 0.2), contrast_limit=(-0.2, 0.2), p=0.7),
            A.CLAHE(clip_limit=(1, 4), p=0.5), # used in medical imaging (scientific imaging)
            A.OneOf([
               A.GaussNoise(var_limit=[10, 50]),
               A.GaussianBlur(),
               A.MotionBlur(),
               A.MedianBlur(),
            ], p=0.2),
            A.Resize(CFG.size, CFG.size),
            A.OneOf([
                JpegCompression(),
                Downscale(scale_min=0.1, scale_max=0.15),
            ], p=0.3),
           
            A.Normalize(
                mean=[0.485, 0.456, 0.406],
                std=[0.229, 0.224, 0.225],
            ),
            ToTensorV2()
        ])
    
    elif data == 'valid':
        return A.Compose([
                Resize(CFG.size, CFG.size),
                Normalize(
                     mean=[0.485, 0.456, 0.406],
                     std=[0.229, 0.224, 0.225],
                 ),
                ToTensorV2()
        ])

In [9]:
from torch.utils.data import DataLoader, Dataset

In [10]:
TRAIN_PATH = '../input/ranzcr-clip-catheter-line-classification/train'

In [11]:
class DatasetRANZCR(Dataset):
    def __init__(self, df, transform=None):
        self.df = df
        self.transform = transform
        self.labels = df[CFG.target_cols].values
        self.filenames = df["StudyInstanceUID"].values
        
    def __len__(self):
        return len(self.df)
        
        
    def __getitem__(self, idx):
        file_name = self.filenames[idx]
        file_path = f"{TRAIN_PATH}/{file_name}.jpg"
       
        image = cv2.imread(file_path)
        image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        if self.transform:
            augmented = self.transform(image=image)
            image = augmented['image']
        label = torch.tensor(self.labels[idx]).float()
        return image, label

In [12]:
from sklearn import preprocessing
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import StratifiedKFold, GroupKFold, KFold

In [13]:
def get_score(y_true, y_pred):
    scores = []
    for i in range(y_true.shape[1]):
        score = roc_auc_score(y_true[:,i], y_pred[:,i])
        scores.append(score)
    avg_score = np.mean(scores)
    return avg_score, scores

In [14]:
def seed_torch(seed=42):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True

seed_torch(seed=CFG.seed)

In [15]:
folds = train.copy()
Fold = GroupKFold(n_splits=CFG.n_fold)
groups = folds['PatientID'].values
for n, (train_index, val_index) in enumerate(Fold.split(folds, folds[CFG.target_cols], groups)):
    folds.loc[val_index, 'fold'] = int(n)
folds['fold'] = folds['fold'].astype(int)
display(folds.groupby('fold').size())

fold
0    7521
1    7521
2    7521
3    7520
dtype: int64

In [16]:
import torch.nn as nn
import torchvision
import torch.nn.functional as F
import torchvision.transforms as transforms
import torch.optim as optim
from torch.optim.lr_scheduler import ReduceLROnPlateau

In [17]:
!pip install timm
import timm

     |████████████████████████████████| 376 kB 281 kB/s eta 0:00:01


In [18]:
class RANZCRModel(nn.Module):
    def __init__(self, model_name=CFG.model_name, out_dim=11, pretrained=False):
        super().__init__()
        self.model = timm.create_model(model_name, pretrained=pretrained)
        n_features = self.model.fc.in_features
        self.model.global_pool = nn.Identity()
        self.model.fc = nn.Identity()
        self.pooling = nn.AdaptiveAvgPool2d(1)
        self.fc = nn.Linear(n_features, out_dim)  
        
    def forward(self, x):
        bs = x.size(0)
        features = self.model(x)
        pooled_features = self.pooling(features).view(bs, -1)
        output = self.fc(pooled_features)
        return output

In [19]:
test = pd.read_csv('../input/ranzcr-clip-catheter-line-classification/sample_submission.csv')


test_dataset = DatasetRANZCR(test, transform=get_transform(data="test"))
test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=CFG.batch_size, shuffle=False,  num_workers=CFG.num_workers)


In [20]:
from albumentations import *

In [21]:
train_dataset = DatasetRANZCR(train, transform=get_transform(data="train"))
train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=CFG.batch_size, shuffle=True, num_workers=CFG.num_workers)

/opt/conda/lib/python3.7/site-packages/albumentations/augmentations/transforms.py:915: FutureWarning: This class has been deprecated. Please use ImageCompression
  FutureWarning,


In [22]:
class AverageMeter(object):
    """Computes and stores the average and current value"""
    def __init__(self):
        self.reset()

    def reset(self):
        self.val = 0
        self.avg = 0
        self.sum = 0
        self.count = 0

    def update(self, val, n=1):
        self.val = val
        self.sum += val * n
        self.count += n
        self.avg = self.sum / self.count

def asMinutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)

def timeSince(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (remain %s)' % (asMinutes(s), asMinutes(rs))

In [23]:
from tqdm.auto import tqdm
from functools import partial

import cv2

from PIL import Image

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.optim import Adam, SGD
import torchvision.models as models
from torch.nn.parameter import Parameter
from torch.utils.data import DataLoader, Dataset
from torch.optim.lr_scheduler import ReduceLROnPlateau

import timm

from torch.cuda.amp import autocast, GradScaler

import warnings 
warnings.filterwarnings('ignore')

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [32]:
def train_fn(train_loader, model, criterion, optimizer, epoch, schedular, device):
    scaler = GradScaler()
    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()
    scores = AverageMeter()
    model.train()
    
    start=end=time.time()
    global_step=0
    for step, (images, labels) in enumerate(train_loader):
        data_time.update(time.time()-end)
        images, labels = images.to(device), labels.to(device)
        batch_size = labels.size(0)
        with autocast():
            y_preds = model(images)
            loss = criterion(y_preds, labels)
        losses.update(loss.item(), batch_size)
        if CFG.gradient_accumulation_steps > 1:
            loss = loss / CFG.gradient_accumulation_steps
        scaler.scale(loss).backward()
        grad_norm = torch.nn.utils.clip_grad_norm_(model.parameters(), CFG.max_grad_norm)
        if (step + 1) % CFG.gradient_accumulation_steps == 0:
            scaler.step(optimizer)
            scaler.update()
            optimizer.zero_grad()
            global_step += 1
        batch_time.update(time.time() - end)
        end = time.time()
        if step % CFG.print_freq == 0 or step == (len(train_loader)-1):
            print('Epoch: [{0}][{1}/{2}] '
                  'Data {data_time.val:.3f} ({data_time.avg:.3f}) '
                  'Elapsed {remain:s} '
                  'Loss: {loss.val:.4f}({loss.avg:.4f}) '
                  'Grad: {grad_norm:.4f}  '
                  #'LR: {lr:.6f}  '
                  .format(
                   epoch+1, step, len(train_loader), batch_time=batch_time,
                   data_time=data_time, loss=losses,
                   remain=timeSince(start, float(step+1)/len(train_loader)),
                   grad_norm=grad_norm,
                   #lr=scheduler.get_lr()[0],
                   ))
    return losses.avg

In [25]:
def valid_fn(valid_loader, model, criterion, device):
    batch_time = AverageMeter()
    data_time = AverageMeter()
    losses = AverageMeter()
    scores = AverageMeter()
    # switch to evaluation mode
    model.eval()
    preds=[]
    start=end=time.time()
    for step, (images, labels) in enumerate(test_loader):
        data_time.update(time.time() - end)
        images = images.to(device)
        labels = labels.to(device)
        batch_size = labels.size(0)
        
        with torch.no_grad():
            y_preds = model(images)
        loss = criterion(y_preds, labels)
        losses.update(loss.item(), batch_size)
        # record accuracy
        preds.append(y_preds.sigmoid().to('cpu').numpy())
        if CFG.gradient_accumulation_steps > 1:
            loss = loss / CFG.gradient_accumulation_steps
        # measure elapsed time
        batch_time.update(time.time() - end)
        end = time.time()
        if step % CFG.print_freq == 0 or step == (len(valid_loader)-1):
            print('EVAL: [{0}/{1}] '
                  'Data {data_time.val:.3f} ({data_time.avg:.3f}) '
                  'Elapsed {remain:s} '
                  'Loss: {loss.val:.4f}({loss.avg:.4f}) '
                  .format(
                   step, len(valid_loader), batch_time=batch_time,
                   data_time=data_time, loss=losses,
                   remain=timeSince(start, float(step+1)/len(valid_loader)),
                   ))
    predictions = np.concatenate(preds)
    return losses.avg, predictions

In [26]:
import os
import math
import time
import random
import shutil
from pathlib import Path
from contextlib import contextmanager
from collections import defaultdict, Counter

In [27]:
import os

OUTPUT_DIR = './'
if not os.path.exists(OUTPUT_DIR):
    os.makedirs(OUTPUT_DIR)

#TRAIN_PATH = '../input/ranzcr-512x512-dataset'
TRAIN_PATH = '../input/ranzcr-clip-catheter-line-classification/train'

In [28]:
@contextmanager
def timer(name):
    t0 = time.time()
    LOGGER.info(f'[{name}] start')
    yield
    LOGGER.info(f'[{name}] done in {time.time() - t0:.0f} s.')


def init_logger(log_file=OUTPUT_DIR+'train.log'):
    from logging import getLogger, INFO, FileHandler,  Formatter,  StreamHandler
    logger = getLogger(__name__)
    logger.setLevel(INFO)
    handler1 = StreamHandler()
    handler1.setFormatter(Formatter("%(message)s"))
    handler2 = FileHandler(filename=log_file)
    handler2.setFormatter(Formatter("%(message)s"))
    logger.addHandler(handler1)
    logger.addHandler(handler2)
    return logger

LOGGER = init_logger()

In [29]:
def train_loop(folds, fold):
    
    LOGGER.info(f"======== fold: {fold} training ========")
    trn_idx = folds[folds['fold'] != fold].index
    val_idx = folds[folds['fold'] == fold].index

    train_folds = folds.loc[trn_idx].reset_index(drop=True)
    valid_folds = folds.loc[val_idx].reset_index(drop=True)
    valid_labels = valid_folds[CFG.target_cols].values
    
    train_dataset = DatasetRANZCR(train_folds, 
                                 transform=get_transform(data='train'))
    valid_dataset = DatasetRANZCR(valid_folds, 
                                 transform=get_transform(data='valid'))

    train_loader = DataLoader(train_dataset, 
                              batch_size=CFG.batch_size, 
                              shuffle=True, 
                              num_workers=CFG.num_workers, pin_memory=True, drop_last=True)
    valid_loader = DataLoader(valid_dataset, 
                              batch_size=CFG.batch_size * 2, 
                              shuffle=False, 
                              num_workers=CFG.num_workers, pin_memory=True, drop_last=False)
    
    def get_scheduler(optimizer):
        return  ReduceLROnPlateau(optimizer, mode='min', factor=CFG.factor, patience=CFG.patience, verbose=True, eps=CFG.eps)
    
    model = RANZCRModel(pretrained=True)
    model.to(device)
    
    optimizer = Adam(model.parameters(), lr=CFG.lr, weight_decay=CFG.weight_decay, amsgrad=False)
    scheduler = get_scheduler(optimizer)
    criterion = nn.BCEWithLogitsLoss()
    
    best_score = 0
    best_loss = np.inf
    
    for epoch in range(CFG.epochs):
        
        start_time = time.time()
        avg_loss = train_fn(train_loader, model, criterion, optimizer, epoch, scheduler, device)

        # eval
        avg_val_loss, preds = valid_fn(valid_loader, model, criterion, device)
        
        schedular.step(avg_val_loss)
        
        score, scores = get_score(valid_labels, preds)

        elapsed = time.time() - start_time
        LOGGER.info(f'Epoch {epoch+1} - avg_train_loss: {avg_loss:.4f}  avg_val_loss: {avg_val_loss:.4f}  time: {elapsed:.0f}s')
        LOGGER.info(f'Epoch {epoch+1} - Score: {score:.4f}  Scores: {np.round(scores, decimals=4)}')
        
        if avg_val_loss < best_loss:
            best_loss = avg_val_loss
            LOGGER.info(f'Epoch {epoch+1} - Save Best Loss: {best_loss:.4f} Model')
            torch.save({'model': model.state_dict(), 
                        'preds': preds},
                        OUTPUT_DIR+f'{CFG.model_name}_fold{fold}_best.pth')
    
    check_point = torch.load(OUTPUT_DIR+f'{CFG.model_name}_fold{fold}_best.pth')
    for c in [f'pred_{c}' for c in CFG.target_cols]:
        valid_folds[c] = np.nan
    valid_folds[[f'pred_{c}' for c in CFG.target_cols]] = check_point['preds']

    return valid_folds

In [30]:
def main():

    """
    Prepare: 1.train  2.folds
    """

    def get_result(result_df):
        preds = result_df[[f'pred_{c}' for c in CFG.target_cols]].values
        labels = result_df[CFG.target_cols].values
        score, scores = get_score(labels, preds)
        LOGGER.info(f'Score: {score:<.4f}  Scores: {np.round(scores, decimals=4)}')
    
    if CFG.train:
        # train 
        oof_df = pd.DataFrame()
        for fold in range(CFG.n_fold):
            if fold in CFG.trn_fold:
                _oof_df = train_loop(folds, fold)
                oof_df = pd.concat([oof_df, _oof_df])
                LOGGER.info(f"========== fold: {fold} result ==========")
                get_result(_oof_df)
        # CV result
        LOGGER.info(f"========== CV ==========")
        get_result(oof_df)
        # save result
        oof_df.to_csv(OUTPUT_DIR+'oof_df.csv', index=False)

In [ ]:
if __name__ == '__main__':
    main()

======== fold: 0 training ========


Epoch: [1][0/1410] Data 4.398 (4.398) Elapsed 0m 13s (remain 308m 20s) Loss: 0.6975(0.6975) Grad: 69820.1250  
Epoch: [1][100/1410] Data 0.000 (0.044) Elapsed 14m 1s (remain 181m 45s) Loss: 0.2486(0.3441) Grad: 86655.6797  
Epoch: [1][200/1410] Data 0.000 (0.022) Elapsed 27m 50s (remain 167m 28s) Loss: 0.2320(0.3044) Grad: 43718.2227  
Epoch: [1][300/1410] Data 0.000 (0.015) Elapsed 41m 39s (remain 153m 28s) Loss: 0.2952(0.2921) Grad: 48217.6758  
Epoch: [1][400/1410] Data 0.000 (0.011) Elapsed 55m 27s (remain 139m 33s) Loss: 0.2933(0.2812) Grad: 73121.2344  
